### Jacopo Sala 
### HYCOM GOFS 3.0: HYCOM + NCODA Global 1/12° Analysis
#### Date Range: 2008-09-19 to 2018-11-20


In [1]:
import xarray as xr
import csv
import pandas as pd
import pickle
import numpy as np
import os
from datetime import datetime, date, timedelta
import sys
import matplotlib.pyplot as plt
import netCDF4 as nc


In [2]:
# input TC tracks
track_dir = '/Users/jacoposala/Desktop/CU/3.RESEARCH/ARGO_analysis/Inputs/'
basin_list = ['HURDAT_PACIFIC.csv', 'HURDAT_ATLANTIC.csv', 'JTWC_INDIANOCEAN.csv', 'JTWC_SOUTHERNHEMISPHERE.csv', 'JTWC_WESTPACIFIC.csv']
# define start and end years
start_year = 2009 # 2009
end_year = 2018
# days_to_save =  [-20, -15, -12 ,-10, -7, -5, -2, 0, 2, 5, 7, 10, 12, 15, 20] # add +- 12, 15, 20 days
days_to_save =  [-5, -2, 0, 2, 5] # add +- 12, 15, 20 days
var_names_download = ['temp', 'salt']
var_names = ['temperature', 'salinity']
# HYCOM_dir = '/Users/jacoposala/Desktop/CU/3.RESEARCH/ARGO_analysis/TC_HYCOM/DATA'
HYCOM_dir = '/Volumes/Backup/HYCOM_RAW_DATA/'
HYCOM_save_dir = '/Users/jacoposala/Desktop/CU/3.RESEARCH/ARGO_analysis/TC_HYCOM/DATA/HYCOM_near_TC_pkl/'


# HYCOM_dir_input = '/Users/jacoposala/Desktop/CU/3.RESEARCH/ARGO_analysis/TC_HYCOM/DATA/HYCOM_raw_data/'
HYCOM_dir_input = '/Volumes/Backup/HYCOM_RAW_DATA/'
url_prefix='ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/VAR_to_set/'
tag_file = 'HYCOM_GBLa0.08'
file_prefix='rarchv.'
file_suffix='_00_3z'
hycom_levels = 10
file_extension='.nc4'
max_depth_index_sel = 10 # 10 or 11 depth levels 
min_wind_knots = 64


In [3]:
# import TC tracks, concatenate into a single dataframe
filesnames = os.listdir(track_dir)
dfs = list()
for filename in basin_list:
     df = pd.read_csv(track_dir + filename)
     dfs.append(df)
dfs = pd.concat(dfs, axis=0, ignore_index=True)
# convert timestamp to datetime
dfs['DATETIME'] = pd.to_datetime(dfs['TIMESTAMP'])
# sort df elements by datetime in chronological order
dfs_sorted = dfs.sort_values(by='DATETIME')

In [6]:
# keep only some relevant columns
dfs_lessclmns = dfs_sorted.drop(columns=['NAME', 'TIME', 'L', 'CLASS', 'PRESS', 'NUM'])

# create mask based on start_year
dfs_mask_1 = dfs_lessclmns['SEASON']>=start_year
# apply mask start_year to df
dfs_1 = dfs_lessclmns[dfs_mask_1].reset_index()

# create mask based on end_year
dfs_mask_2 = dfs_1['SEASON']<=end_year
# apply mask end_year to df
dfs_select = dfs_1[dfs_mask_2].reset_index()
dfs_select.shape
dfs_select['DATE'] = pd.to_datetime(dfs_select['DATE'])
dfs_select.to_pickle('dfs_select.pkl')
# dfs_select

In [ ]:
sum(dfs_select.WIND>= 64)

In [ ]:
dfs_select

In [ ]:

from cartopy import config
import cartopy.crs as ccrs

ax = plt.axes(projection=ccrs.PlateCarree())

plt.plot(dfs_select.LONG[dfs_select.WIND>= 64], dfs_select.LAT[dfs_select.WIND>= 64], '*', transform=ccrs.PlateCarree())

ax.coastlines()


In [7]:
# def distance(lat1, lon1, lat2, lon2):
#      p = 0.017453292519943295
#      hav = 0.5 - np.cos((lat2-lat1)*p)/2 + np.cos(lat1*p)*np.cos(lat2*p) * (1-np.cos((lon2-lon1)*p)) / 2
#      return 12742 * np.arcsin(np.sqrt(hav))

def upload_model_dataset(date, delta_days, url_prefix, file_prefix, file_suffix, f_dir):
    year = date[0:4]
    month = date[5:7]
    day = date[8:10]
    date = datetime(int(year), int(month), int(day)) + timedelta(days=delta_days)
    day_of_year = date.timetuple().tm_yday 
    day_of_year = f"{int(day_of_year):03d}"
    year = f"{int(date.year):04d}"
    month = f"{int(date.month):02d}"
    day = f"{int(date.day):02d}"
    print(f'{url_prefix}{year}_{day_of_year}{file_suffix}')
    !wget -nc --directory-prefix={f_dir} {url_prefix}{file_prefix}{year}_{day_of_year}{file_suffix}
    dset_day = xr.open_dataset(f'{f_dir}{file_prefix}{year}_{day_of_year}{file_suffix}')
    return(dset_day)

def define_array_T_S(bfr_select, days_to_save):
    arr=np.zeros((hycom_levels,len(days_to_save),len(bfr_select)))
    for irow in np.arange(0,len(bfr_select),1):
        n=0
        for i in bfr_select:
            if len(bfr_select[i][irow]) == 1: # if it's not all Nans
                arr[:,n,irow]=bfr_select[i][irow][0][0:max_depth_index_sel]
                
#                 if len(bfr_select[i][irow][0]) > hycom_levels: # if 11 pressure levels
#                     arr[:,n,irow]=bfr_select[i][irow][0][0:-1] # save the first 10 levels
#                 else: # if 10 pressure levels
#                     arr[:,n,irow]=bfr_select[i][irow][0] # save them all

            else: # if it's all Nans
                arr[:,n,irow]=np.nan
            n = n+1
    return arr


In [8]:
# create a list of unique days only
yymmdd_str = dfs_select["DATETIME"].dt.strftime('%Y-%m-%d').unique() 

In [ ]:
# df_bfr_all.drop_duplicates(subset=["WIND"])>=64

In [9]:

############################ TEST #############################
# Main loop  
for x in yymmdd_str: # loop through all unique days 
    print(x)
    # Select TC data for the specific date being considered
    df_bfr_all = dfs_select[dfs_select['DATE'].dt.strftime('%Y-%m-%d').str.contains(x)]
    # Remove ID duplicates, keeping the first TC only (first TC for every unique day and every unique TC)
    # add selection based on the strongest wind for every day
    df_on_TC_track = df_bfr_all.drop_duplicates(subset=["ID"]).reset_index(drop=True)
#     df_on_TC_track = df_bfr_all.drop_duplicates(subset=["ID"], keep='first').reset_index(drop=True)
#     CIAO
    # Latitude and longitudes of single TCs on this date
    lat = df_on_TC_track['LAT']
    lon = df_on_TC_track['LONG']
    for iday in days_to_save: # loop over iday: -5, 0, 5
        for ivar, namevar in zip(var_names_download,var_names): # loop over variables (temp or salt)
            column_name = 'day_' + str(iday) + '_' + str(namevar)
            # Initialize new column and populate with NaNs for now
            df_on_TC_track[column_name] = [[np.nan]*hycom_levels]*df_on_TC_track.shape[0]
            # download HYCOM data
            bfr_url = url_prefix.replace('VAR_to_set', ivar) # change var to download (temp or salt)
            bfr_dset = upload_model_dataset(x, delta_days=iday, url_prefix=bfr_url, file_prefix=file_prefix, 
                                            file_suffix=file_suffix+ivar[0]+file_extension, f_dir=HYCOM_dir_input)
            
            # change longitude from 74/434 to -180/+180
            bfr_dset = bfr_dset.assign_coords(Longitude=
                                              (((bfr_dset.Longitude + 180) % 360) - 180))
            bfr_dset = bfr_dset.loc[{'Longitude':sorted(bfr_dset.coords['Longitude'].values)}]
            print(float(bfr_dset.Longitude.min().values))
            print(float(bfr_dset.Longitude.max().values))
            
            # Loop across all lat-lon where a TC is recorded on this date and find nearest HYCOM data point
            for i in np.arange(len(lat)):
                ilon=lon[i]
                ilat=lat[i]
                # Interpolate HYCOM data
                data_on_track = bfr_dset.interp(Longitude=[ilon], Latitude=[ilat])[namevar].values.flatten().tolist()
                # Find the relevant TC data point (date, lat and lon being considered)
                mask = (df_on_TC_track['DATE'].dt.strftime('%Y-%m-%d').str.contains(x)).values & \
                (df_on_TC_track['LONG']==ilon).values & (df_on_TC_track['LAT']==ilat).values
                # Populate relevant row in df_on_TC_track (if the interpolation gave some not-Nans)
                if sum(np.isnan(data_on_track))!=len(data_on_track):
                    df_on_TC_track.loc[mask,column_name] = [[data_on_track]]
                    
    # Save daily files with HYCOM data near TCs
    index = np.arange(0,len(df_on_TC_track),1)

    for ivar in ['temperature','salinity']:
        lst = []
        for i_dtime in days_to_save:
            lst.append('day_'+str(i_dtime)+'_'+ivar)
        bfr_select = df_on_TC_track[df_on_TC_track.columns.intersection(lst)]   
        bfr = define_array_T_S(bfr_select, days_to_save)
        exec(ivar+'= bfr')
    
    d_xr = xr.Dataset(
        data_vars=dict(
            ID=(["index"], df_on_TC_track.ID,{'label': 'ID TCs'}),
            longitude=(["index"], df_on_TC_track.LONG),
            latitude=(["index"], df_on_TC_track.LAT),
            time=(["index"], df_on_TC_track.TIMESTAMP),
            wind=(["index"], df_on_TC_track.WIND),
            temperature=(["depth", "delta_time", "index"], temperature ,{'label': 'HYCOM T at TC location'}),
            salinity=(["depth", "delta_time", "index"], salinity,{'label': 'HYCOM S at TC location'}),

        ),
        coords=dict(
            index=index,
            depth=bfr_dset.Depth.values[0:10],
            delta_time=days_to_save,
        ),
        attrs=dict(description="HYCOM T/S co-located with TCs"),
        )
    with open(HYCOM_save_dir+tag_file+'_'+x+'.pkl', 'wb') as handle:
        pickle.dump(d_xr, handle, protocol=pickle.HIGHEST_PROTOCOL)
#     d_xr.to_pickle(f'{HYCOM_dir}/{tag_file}_{x}.pkl')

#     df_on_TC_track.to_csv(f'{HYCOM_dir}/HYCOM_near_TC_csv/{tag_file}_{x}.csv', index=False)        



2009-01-01
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2008_362_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2008_362_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2008_362_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2008_362_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2008_365_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2008_365_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2008_365_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2008_365_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_001_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_001_00_3zt.nc4' already there; not retrieving.
-180

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_003_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_003_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_006_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_006_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_006_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_006_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_008_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_008_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_008_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_008_00_3zs.nc4' already there; not re

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_010_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_010_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_010_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_010_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_012_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_012_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_012_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_012_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_014_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_014_00_3zt.nc4' already there; not re

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_016_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_016_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_018_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_018_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_018_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_018_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_020_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_020_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_020_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_020_00_3zs.nc4' already there; not re

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_022_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_022_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_022_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_022_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_024_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_024_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2009_024_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_024_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2009_027_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2009_027_00_3zt.nc4' already there; not re

...

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_310_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_310_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_310_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_310_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_312_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_312_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_312_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_312_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_314_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_314_00_3zt.nc4' already there; not re

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_314_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_314_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_316_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_316_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_316_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_316_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_318_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_318_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_318_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_318_00_3zs.nc4' already there; not re

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_320_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_320_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_320_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_320_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_322_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_322_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_322_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_322_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_325_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_325_00_3zt.nc4' already there; not re

-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_324_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_324_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_326_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_326_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_326_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_326_00_3zs.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/temp/2018_329_00_3zt.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_329_00_3zt.nc4' already there; not retrieving.
-180.0
179.9200439453125
ftp://ftp.hycom.org//datasets/global/GLBa0.08_rect/data/salt/2018_329_00_3zs.nc4
File '/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_329_00_3zs.nc4' already there; not re

FileNotFoundError: [Errno 2] No such file or directory: b'/Volumes/Backup/HYCOM_RAW_DATA/rarchv.2018_332_00_3zt.nc4'

In [ ]:
# Main loop  
for x in yymmdd_str: # loop through all unique days 
    print(x)
    # Select TC data for the specific date being considered
    df_bfr_all = dfs_select[dfs_select['DATE'].dt.strftime('%Y-%m-%d').str.contains(x)]
    # Remove ID duplicates, keeping the first TC only (first TC for every unique day and every unique TC)
    # add selection based on the strongest wind for every day
    df_on_TC_track = df_bfr_all.drop_duplicates(subset=["ID"], keep='first').reset_index(drop=True)
    # Latitude and longitudes of single TCs on this date
    lat = df_on_TC_track['LAT']
    lon = df_on_TC_track['LONG']
    for iday in days_to_save: # loop over iday: -5, 0, 5
        for ivar, namevar in zip(var_names_download,var_names): # loop over variables (temp or salt)
            column_name = 'day_' + str(iday) + '_' + str(namevar)
            # Initialize new column and populate with NaNs for now
            df_on_TC_track[column_name] = [[np.nan]*hycom_levels]*df_on_TC_track.shape[0]
            # download HYCOM data
            bfr_url = url_prefix.replace('VAR_to_set', ivar) # change var to download (temp or salt)
            bfr_dset = upload_model_dataset(x, delta_days=iday, url_prefix=bfr_url, file_prefix=file_prefix, 
                                            file_suffix=file_suffix+ivar[0]+file_extension, f_dir=HYCOM_dir_input)
            
            # change longitude from 74/434 to -180/+180
            bfr_dset = bfr_dset.assign_coords(Longitude=
                                              (((bfr_dset.Longitude + 180) % 360) - 180))
            bfr_dset = bfr_dset.loc[{'Longitude':sorted(bfr_dset.coords['Longitude'].values)}]
            print(float(bfr_dset.Longitude.min().values))
            print(float(bfr_dset.Longitude.max().values))
            
            # Loop across all lat-lon where a TC is recorded on this date and find nearest HYCOM data point
            for i in np.arange(len(lat)):
                ilon=lon[i]
                ilat=lat[i]
                # Interpolate HYCOM data
                data_on_track = bfr_dset.interp(Longitude=[ilon], Latitude=[ilat])[namevar].values.flatten().tolist()
                # Find the relevant TC data point (date, lat and lon being considered)
                mask = (df_on_TC_track['DATE'].dt.strftime('%Y-%m-%d').str.contains(x)).values & \
                (df_on_TC_track['LONG']==ilon).values & (df_on_TC_track['LAT']==ilat).values
                # Populate relevant row in df_on_TC_track (if the interpolation gave some not-Nans)
                if sum(np.isnan(data_on_track))!=len(data_on_track):
                    df_on_TC_track.loc[mask,column_name] = [[data_on_track]]
                    
    # Save daily files with HYCOM data near TCs
    index = np.arange(0,len(df_on_TC_track),1)

    for ivar in ['temperature','salinity']:
        lst = []
        for i_dtime in days_to_save:
            lst.append('day_'+str(i_dtime)+'_'+ivar)
        bfr_select = df_on_TC_track[df_on_TC_track.columns.intersection(lst)]   
        bfr = define_array_T_S(bfr_select, days_to_save)
        exec(ivar+'= bfr')
    
    d_xr = xr.Dataset(
        data_vars=dict(
            ID=(["index"], df_on_TC_track.ID,{'label': 'ID TCs'}),
            longitude=(["index"], df_on_TC_track.LONG),
            latitude=(["index"], df_on_TC_track.LAT),
            time=(["index"], df_on_TC_track.TIMESTAMP),
            wind=(["index"], df_on_TC_track.WIND),
            temperature=(["depth", "delta_time", "index"], temperature ,{'label': 'HYCOM T at TC location'}),
            salinity=(["depth", "delta_time", "index"], salinity,{'label': 'HYCOM S at TC location'}),

        ),
        coords=dict(
            index=index,
            depth=bfr_dset.Depth.values[0:10],
            delta_time=days_to_save,
        ),
        attrs=dict(description="HYCOM T/S co-located with TCs"),
        )
    with open(HYCOM_save_dir+tag_file+'_'+x+'.pkl', 'wb') as handle:
        pickle.dump(d_xr, handle, protocol=pickle.HIGHEST_PROTOCOL)
#     d_xr.to_pickle(f'{HYCOM_dir}/{tag_file}_{x}.pkl')

#     df_on_TC_track.to_csv(f'{HYCOM_dir}/HYCOM_near_TC_csv/{tag_file}_{x}.csv', index=False)        


In [ ]:
bfr_dset.Depth[0:10]

In [ ]:
arr=np.empty((10,len(days_to_save),len(bfr_select)))
for irow in np.arange(0,len(bfr_select),1):
    n=0
    for i in bfr_select:
        if len(bfr_select[i][irow]) == 1:
            if len(bfr_select[i][irow][0]) >10:
                arr[:,n,irow]=bfr_select[i][irow][0][0:-1]
            else:
                arr[:,n,irow]=bfr_select[i][irow][0]
        n = n+1

In [ ]:
# Main loop  
x = yymmdd_str[1675] # loop through all unique days 
print(x)
# Select TC data for the specific date being considered
df_bfr_all = dfs_select[dfs_select['DATE'].dt.strftime('%Y-%m-%d').str.contains(x)]
# Remove ID duplicates, keeping the first TC only (first TC for every unique day and every unique TC)
df_on_TC_track = df_bfr_all.drop_duplicates(subset=["ID"], keep='first').reset_index(drop=True)
# Latitude and longitudes of single TCs on this date
lat = df_on_TC_track['LAT']
lon = df_on_TC_track['LONG']
for iday in days_to_save: # loop over iday: -5, 0, 5
    for ivar, namevar in zip(var_names_download,var_names): # loop over variables (temp or salt)
        column_name = 'day_' + str(iday) + '_' + str(namevar)
        # Initialize new column and populate with NaNs for now
        df_on_TC_track[column_name] = [[np.nan]*hycom_levels]*df_on_TC_track.shape[0]
        # download HYCOM data
        bfr_url = url_prefix.replace('VAR_to_set', ivar) # change var to download (temp or salt)
        bfr_dset = upload_model_dataset(x, delta_days=iday, url_prefix=bfr_url, file_prefix=file_prefix, 
                                        file_suffix=file_suffix+ivar[0]+file_extension, f_dir=HYCOM_dir_input)

        # change longitude from 74/434 to -180/+180
        bfr_dset = bfr_dset.assign_coords(Longitude=
                                          (((bfr_dset.Longitude + 180) % 360) - 180))
        bfr_dset = bfr_dset.loc[{'Longitude':sorted(bfr_dset.coords['Longitude'].values)}]
        print(float(bfr_dset.Longitude.min().values))
        print(float(bfr_dset.Longitude.max().values))

        # Loop across all lat-lon where a TC is recorded on this date and find nearest HYCOM data point
        for i in np.arange(len(lat)):
            ilon=lon[i]
            ilat=lat[i]
            # Interpolate HYCOM data
            data_on_track = bfr_dset.interp(Longitude=[ilon], Latitude=[ilat])[namevar].values.flatten().tolist()
            # Find the relevant TC data point (date, lat and lon being considered)
            mask = (df_on_TC_track['DATE'].dt.strftime('%Y-%m-%d').str.contains(x)).values & (df_on_TC_track['LONG']==ilon).values & (df_on_TC_track['LAT']==ilat).values
            # Populate relevant row in df_on_TC_track (if the interpolation gave some not-Nans)
            if sum(np.isnan(data_on_track))!=len(data_on_track):
                df_on_TC_track.loc[mask,column_name] = [[data_on_track]]
                    

In [ ]:
# Save daily files with HYCOM data near TCs
index = np.arange(0,len(df_on_TC_track),1)

for ivar in ['temperature','salinity']:
    lst = []
    for i_dtime in days_to_save:
        lst.append('day_'+str(i_dtime)+'_'+ivar)
    bfr_select = df_on_TC_track[df_on_TC_track.columns.intersection(lst)]   
    bfr = define_array_T_S(bfr_select, days_to_save)
    exec(ivar+'= bfr')

In [ ]:
bfr_select

In [ ]:
bfr_select["day_-5_salinity"][0]

In [ ]:
days_to_save

In [ ]:
bfr

In [ ]:
len(bfr_select[i][1])

In [ ]:
arr=np.zeros((10,len(days_to_save),len(bfr_select)))
for irow in np.arange(0,len(bfr_select),1):
    n=0
    for i in bfr_select:
        if len(bfr_select[i][irow]) == 1:
            if len(bfr_select[i][irow][0]) >10:
                arr[:,n,irow]=bfr_select[i][irow][0][0:-1]
            else:
                arr[:,n,irow]=bfr_select[i][irow][0]
        else: 
            arr[:,n,irow]=np.nan
        n = n+1


In [ ]:
bfr_select

In [ ]:
arr

In [ ]:

arr=np.empty((len(bfr_dset.Depth.values),len(days_to_save),len(bfr_select)))
for irow in np.arange(0,len(bfr_select),1):
    print(irow)
    n=0
    for i in bfr_select:
        print(i)
        if len(bfr_select[i][irow]) == 1:
            print('This case')
            arr[:,n,irow]=bfr_select[i][irow][0]
        n = n+1

In [ ]:
np.arange(0,len(bfr_select),1)

In [ ]:
arr

In [ ]:
salinity.shape

In [ ]:
d_xr = xr.Dataset(
    data_vars=dict(
        ID=(["index"], df_on_TC_track.ID,{'label': 'ID TCs'}),
        longitude=(["index"], df_on_TC_track.LONG),
        latitude=(["index"], df_on_TC_track.LAT),
        time=(["index"], df_on_TC_track.TIMESTAMP),
        wind=(["index"], df_on_TC_track.WIND),
        temperature=(["depth", "delta_time", "index"], temperature ,{'label': 'HYCOM T at TC location'}),
        salinity=(["depth", "delta_time", "index"], salinity,{'label': 'HYCOM S at TC location'}),

    ),
    coords=dict(
        index=index,
        depth=bfr_dset.Depth.values,
        delta_time=days_to_save,
    ),
    attrs=dict(description="HYCOM T/S co-located with TCs"),
    )
with open(HYCOM_save_dir+tag_file+'_'+HYCOM_release+'_'+x+'.pkl', 'wb') as handle:
    pickle.dump(d_xr, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [ ]:
# # Create a pandas dataframe such that we have one Tc track per each day (one single dataframe, one TC track point for each TC)
# df_tracks = pd.DataFrame()
# for x in yymmdd_str: # loop through all unique days
#     # Select TC data for the specific date being considered
#     df_bfr_all = dfs_select[dfs_select['DATE'].str.contains(x)]
#     # Remove ID duplicates, keeping the first TC only (first TC for every unique day and every unique TC)
#     df_tracks = df_tracks.append(df_bfr_all.drop_duplicates(subset=["ID"], keep='first'))
# # Initialize new column a populate with NaNs for now
# df_on_TC_track['day_0_temperature'] = [[np.nan]*hycom_levels]*df_to_save.shape[0]
# df_on_TC_track['day_5_temperature'] = [[np.nan]*hycom_levels]*df_to_save.shape[0]
# df_on_TC_track['day_-5_temperature'] = [[np.nan]*hycom_levels]*df_to_save.shape[0]
# df_on_TC_track['day_0_salinity'] = [[np.nan]*hycom_levels]*df_to_save.shape[0]
# df_on_TC_track['day_5_salinity'] = [[np.nan]*hycom_levels]*df_to_save.shape[0]
# df_on_TC_track['day_-5_salinity'] = [[np.nan]*hycom_levels]*df_to_save.shape[0]


In [ ]:
#                 # Calculate distance of HYCOM data from TC tracks' lat/lon 
#                 dist_array = distance(lat.iloc[i], lon.iloc[i], bfr_dset[namevar].Latitude, bfr_dset[namevar].Longitude).values
#                 # Create list of indexes of HYCOM grid point(s) closest to TC tracks
#                 index_closest = np.where(dist_array == dist_array.min())
                
#                 if np.shape(index_closest)[1]<2: # if only one HYCOM grid cell is the closest...
#                     # select HYCOM data in the appropriate grid cell
#                     data_nearTC = bfr_dset[namevar][:,:,int(index_closest[0]),int(index_closest[1])].values
#                     # Find the relevant TC data point (date, lat and lon being considered)
#                     mask = (df_to_save['DATE'].str.contains(x)).values & (df_to_save['LONG'] == lon.iloc[i]).values & (df_to_save['LAT']==lat.iloc[i]).values
#                     # Populate relevant row in df_to_save
#                     column_name = 'day_' + str(iday) + '_' + str(namevar)
#                     print(column_name)
#                     df_to_save.loc[mask,column_name] = [[data_nearTC.flatten().tolist()]]  
#                 else: # if we have two equally-distant HYCOM grid cells...
#                     # for two equally distant HYCOM grid cells at day 0
#                     data_nearTC_a = bfr_dset[namevar][:,:,int(index_closest[0][0]),int(index_closest[1][0])].values
#                     data_nearTC_b = bfr_dset[namevar][:,:,int(index_closest[0][1]),int(index_closest[1][1])].values
#                     # if the surface values of two closest cells are greater than zero (=not on land), calculate the mean
#                     if data_nearTC_a[0][0]>0 and data_nearTC_b[0][0]>0:
#                         data_nearTC = (data_nearTC_a + data_nearTC_b)/2
#                     # if the surface value of only one closest cell is greater than zero (=not on land), keep that
#                     elif data_nearTC_a[0][0]>0 and data_nearTC_b[0][0]==0:
#                         data_nearTC = data_nearTC_a 
#                     elif data_nearTC_a[0][0]==0 and data_nearTC_b[0][0]>0:
#                         data_nearTC = data_nearTC_b
#                     # Find the relevant TC data point (date, lat and lon being considered)
#                     mask = (df_to_save['DATE'].str.contains(x)).values & (df_to_save['LONG']==lon.iloc[i]).values & (df_to_save['LAT']==lat.iloc[i]).values
#                     # Populate relevant row in df_to_save
#                     column_name = 'day_' + str(iday) + '_' + str(namevar)
#                     print(column_name)
#                     df_to_save.loc[mask,column_name] = [[data_nearTC.flatten().tolist()]]